In [48]:
import numpy as np
import pandas as pd

In [50]:
data_set = pd.read_csv('Flight_Data.csv')
data_set

Airline                     SourceAirport  \
0      Aerocondor       Sochi International Airport   
1      Aerocondor                 Astrakhan Airport   
2      Aerocondor     Chelyabinsk Balandino Airport   
3      Aerocondor  Domodedovo International Airport   
4      Aerocondor    Belgorod International Airport   
...           ...                               ...   
36515   Iberworld                     Lifou Airport   
36516   Iberworld            Nouméa Magenta Airport   
36517   Iberworld            Nouméa Magenta Airport   
36518   Iberworld                     Lifou Airport   
36519   Iberworld                    Koumac Airport   

                DestinationAirport SourceAirport_City SourceAirport_Country  \
0      Kazan International Airport              Sochi                Russia   
1      Kazan International Airport          Astrakhan                Russia   
2      Kazan International Airport        Chelyabinsk                Russia   
3      Kazan International Airport             Moscow                Russia   
4      Kazan International Airport           Belgorod                Russia   
...                            ...                ...                   ...   
36515                 Tiga Airport              Lifou         New Caledonia   
36516                Touho Airport             Noumea         New Caledonia   
36517                Ouvéa Airport             Noumea         New Caledonia   
36518                Ouvéa Airport              Lifou         New Caledonia   
36519      Île Art - Waala Airport             Koumac         New Caledonia   

       SourceAirport_Latitude  SourceAirport_Longitude  \
0                   43.449902                39.956600   
1                   46.283298                48.006302   
2                   55.305801                61.503300   
3                   55.408798                37.906300   
4                   50.643799                36.590099   
...                       ...                      ...   
36515              -20.774799               167.240005   
36516              -22.258301               166.473007   
36517              -22.258301               166.473007   
36518              -20.774799               167.240005   
36519              -20.546301               164.255997   

       SourceAirport_Altitude DestinationAirport_City  \
0                          89                   Kazan   
1                         -65                   Kazan   
2                         769                   Kazan   
3                         588                   Kazan   
4                         735                   Kazan   
...                       ...                     ...   
36515                      92                    Tiga   
36516                      10                   Touho   
36517                      10                   Ouvea   
36518                      92                   Ouvea   
36519                      42                   Waala   

      DestinationAirport_Country  DestinationAirport_Latitude  \
0                         Russia                    55.606201   
1                         Russia                    55.606201   
2                         Russia                    55.606201   
3                         Russia                    55.606201   
4                         Russia                    55.606201   
...                          ...                          ...   
36515              New Caledonia                   -21.096100   
36516              New Caledonia                   -20.790001   
36517              New Caledonia                   -20.640600   
36518              New Caledonia                   -20.640600   
36519              New Caledonia                   -19.720600   

       DestinationAirport_Longitude  DestinationAirport_Altitude     Distance  \
0                         49.278702                          411  1506.825604   
1                         49.278702                          411  1040.4383

In [66]:
import sys
from queue import PriorityQueue

class Path:
    def __init__(self):
        self.__nodes = []

    @property
    def nodes(self):
        return self.__nodes

    def add_node(self, label: str):
        self.nodes.append(label)

    def __str__(self):
        return f"{self.__nodes}"
        
    
class Node:
    def __init__(self, label: str, city : str, country : str, latitude : str, longitude : str, altitude : str):
        self.__label = label
        self.__city = city
        self.__country = country
        self.__latitude = latitude
        self.__longitude = longitude
        self.__altitude = altitude
        self.__edges = []

    @property
    def edges(self):
        return self.__edges

    @property
    def label(self):
        return self.__label
    
    @property
    def city(self):
        return self.__city
    
    @property
    def country(self):
        return self.__country

    @property
    def latitude(self):
        return self.__latitude
    
    @property
    def longitude(self):
        return self.__longitude
    
    @property
    def altitude(self):
        return self.__altitude
    
    def add_edge(self, target, distance: float, fly_time : float, price : float):
        edge = Edge(self, target, distance, fly_time, price)
        self.edges.append(edge)

    def __str__(self):
        return f"{self.__label}"
    
    
class Edge:

    def __init__(self, from_node: Node, to_node: Node, distance: float, fly_time : float, price : float):
        self.__from_node: Node = from_node
        self.__to_node: Node = to_node
        self.__distance = distance
        self.__fly_time = fly_time
        self.__price = price

    @property
    def from_node(self):
        return self.__from_node

    @property
    def to_node(self):
        return self.__to_node

    @property
    def distance(self):
        return self.__distance
    
    @property
    def fly_time(self):
        return self.__fly_time
    
    @property
    def price(self):
        return self.__price
    
    def __str__(self):
        return f"From : {self.__from_node.city}-{str(self.__from_node)}. {self.__from_node.country}\nTo : {self.__to_node.city}-{str(self.__to_node)}. {self.__to_node.country}\nDistance : {round(self.__distance,2)}\nTime : {round(self.__fly_time, 2)}\nPrice : {round(self.__price, 2)}"
    
    
class WeightedGraph:

    def __init__(self):
        self.__nodes = {}  # key: String  value: Node

    @property
    def nodes(self):
        return self.__nodes

    def add_node(self, label: str, city : str, country : str, latitude : str, longitude : str, altitude : str):
        if label not in self.nodes.keys():
            self.nodes[label] = Node(label, city, country, latitude, longitude, altitude)
        
    def add_edge(self, from_node: str, to_node: str, distance: float, fly_time : float, price : float ):
        origin: Node = self.nodes.get(from_node)
        target: Node = self.nodes.get(to_node)

        if not origin or not target:
            raise Exception("There is not Node for creating Edge")

        origin.add_edge(target, distance, fly_time, price)
    
    @classmethod
    def __build_path(cls, previous: dict, to_node: Node) -> Path:
        stack = [to_node]
        previous_node = previous.get(to_node)

        while previous_node:
            stack.append(previous_node)
            previous_node: Node = previous.get(previous_node)

        p = Path()
        while stack:
            p.add_node(stack.pop().label)

        return p

    def dijkestra(self, from_node, to_node):
        from_node: Node = self.nodes.get(from_node)
        to_node: Node = self.nodes.get(to_node)

        if not from_node or not to_node:
            raise Exception("There is not Node for finding the shortest path")

        distances = dict()  # key: Node  value:  Integer

        for node in self.nodes.values():
            distances[node] = sys.maxsize

        distances[from_node] = 0

        explored = set()

        frontier = PriorityQueue()
        frontier.put((0, from_node))

        previous = dict()  # key: Node  value: Previos Node

        while not frontier.empty():

            current: Node = frontier.get()[1]
            explored.add(current)

            for edge in current.edges:
                if edge.to_node in explored:
                    continue

                new_distance = distances.get(current) + edge.distance + edge.fly_time + edge.price

                if new_distance < distances.get(edge.to_node):
                    distances[edge.to_node] = new_distance
                    previous[edge.to_node] = current
                    frontier.put((new_distance, edge.to_node))

        return WeightedGraph.__build_path(previous, to_node)
    
    def a_star(self, from_node, to_node):
        from_node: Node = self.nodes.get(from_node)
        to_node: Node = self.nodes.get(to_node)

        if not from_node or not to_node:
            raise Exception("There is not Node for finding the shortest path")

        distances = dict()  # key: Node  value:  Integer

        for node in self.nodes.values():
            distances[node] = sys.maxsize

        distances[from_node] = 0

        explored = set()

        frontier = PriorityQueue()
        frontier.put((0, from_node))

        previous = dict()  # key: Node  value: Previos Node

        while not frontier.empty():

            current: Node = frontier.get()[1]
            if current == to_node:
                return WeightedGraph.__build_path(previous, to_node)
            explored.add(current)

            for edge in current.edges:
                if edge.to_node in explored:
                    continue

                new_distance = distances.get(current) + edge.distance + edge.fly_time + edge.price + self.heuristic(current.latitude, current.longitude, current.altitude, to_node.latitude, to_node.longitude, to_node.altitude, 2)

                if new_distance < distances.get(edge.to_node):
                    distances[edge.to_node] = new_distance
                    previous[edge.to_node] = current
                    frontier.put((new_distance, edge.to_node))

        return "There is no such a path."
    
    @staticmethod
    def heuristic(source_airport_latitude : float, source_airport_longitude : float, source_airport_altitude : float, destination_airport_latitude : float, destination_airport_longitude : float, destination_airport_altitude : float, k : int):
        return np.power(np.power(source_airport_latitude - destination_airport_latitude, k) + 
                       np.power(source_airport_longitude - destination_airport_longitude, k) +
                       np.power(source_airport_altitude - destination_airport_altitude, k), -k)
        

In [67]:
#Creating The Graph
golabi = WeightedGraph()
for i in range(len(data_set)):
    sample = data_set.iloc[i]
    golabi.add_node(label = sample.SourceAirport , city = sample.SourceAirport_City, country = sample.SourceAirport_Country, latitude = sample.SourceAirport_Latitude, longitude = sample.SourceAirport_Longitude, altitude = sample.SourceAirport_Altitude)
    golabi.add_node(label = sample.DestinationAirport , city = sample.DestinationAirport_City, country = sample.DestinationAirport_Country, latitude = sample.DestinationAirport_Latitude, longitude = sample.DestinationAirport_Longitude, altitude = sample.DestinationAirport_Altitude)
    golabi.add_edge(from_node = sample.SourceAirport, to_node = sample.DestinationAirport, distance = sample.Distance, fly_time = sample.FlyTime, price = sample.Price)

for sample in golabi.nodes.values():
    sample: Node
    for dample in sample.edges:
        print(dample, end = "\n--------------------------------\n")
        

From : Sochi-Sochi International Airport. Russia
To : Kazan-Kazan International Airport. Russia
Distance : 1506.83
Time : 2.33
Price : 172.66
--------------------------------
From : Sochi-Sochi International Airport. Russia
To : Moscow-Domodedovo International Airport. Russia
Distance : 1337.86
Time : 1.71
Price : 188.13
--------------------------------
From : Sochi-Sochi International Airport. Russia
To : St. Petersburg-Pulkovo Airport. Russia
Distance : 1932.59
Time : 2.69
Price : 230.7
--------------------------------
From : Sochi-Sochi International Airport. Russia
To : Yekaterinburg-Koltsovo Airport. Russia
Distance : 2080.64
Time : 2.65
Price : 285.25
--------------------------------
From : Sochi-Sochi International Airport. Russia
To : Dushanbe-Dushanbe Airport. Tajikistan
Distance : 2470.16
Time : 3.94
Price : 346.48
--------------------------------
From : Sochi-Sochi International Airport. Russia
To : Khudzhand-Khudzhand Airport. Tajikistan
Distance : 2476.5
Time : 4.04
Price 

In [68]:
source, destination = input().split(" - ")
print(golabi.dijkestra(source, destination))

['Imam Khomeini International Airport', 'Zvartnots International Airport', 'Václav Havel Airport Prague', 'Newcastle Airport', 'Melbourne International Airport', 'Charlotte Douglas International Airport', 'Raleigh Durham International Airport']


In [69]:
source, destination = input().split(" - ")
print(golabi.a_star(source, destination))

['Imam Khomeini International Airport', 'Zvartnots International Airport', 'Václav Havel Airport Prague', 'Newcastle Airport', 'Melbourne International Airport', 'Charlotte Douglas International Airport', 'Raleigh Durham International Airport']
